In [29]:
import pandas as pd
import pandas as pd
from datasets import Dataset, DatasetDict
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM
import os
import pandas as pd
from torch.optim import AdamW  # Cambiar esta línea
from transformers import get_linear_schedule_with_warmup
from torch.utils.data import DataLoader
from utils_final import *
from tqdm import tqdm


In [31]:
os.environ["HF_TOKEN"] = ""
os.environ["CUDA_VISIBLE_DEVICES"] ="0"
print(os.environ.get("CUDA_VISIBLE_DEVICES"))

0


## Import Data

In [3]:
data_train= pd.read_csv("/home/msc2024/ra214616/ra214616_files/gabriel_fl_finetuning/FL-LLM-AD/dataset/hdfs/train.csv")
data_test= pd.read_csv("/home/msc2024/ra214616/ra214616_files/gabriel_fl_finetuning/FL-LLM-AD/dataset/hdfs/test.csv")

In [4]:
data_train.loc[data_train["Label"]==0].head()

BlockId  \
0  blk_-2096949670725870127   
1   blk_3256388811978097017   
2   blk_2427220957451379346   
3    blk_436650680792477853   
4  blk_-7199894362523365575   

                                             Content  Label  session_length  
0  Receiving block blk_<*> src: /<*>:<*> dest: /<...      0              19  
1  Receiving block blk_<*> src: /<*>:<*> dest: /<...      0              13  
2  Receiving block blk_<*> src: /<*>:<*> dest: /<...      0              19  
3  Receiving block blk_<*> src: /<*>:<*> dest: /<...      0              19  
4  Receiving block blk_<*> src: /<*>:<*> dest: /<...      0              20

In [5]:
data_train = data_train[data_train['Label'] == 0][0:10]
data_test = data_test[data_test['Label'] == 0][0:10]
# Prepare dataset for Hugging Face
data_train = data_train["Content"].tolist()
data_test = data_test["Content"].tolist()

In [6]:
dataset = DatasetDict({
    "train": Dataset.from_dict({"text": data_train}),
    "test": Dataset.from_dict({"text": data_test})
})

dataset

DatasetDict({
    train: Dataset({
        features: ['text'],
        num_rows: 10
    })
    test: Dataset({
        features: ['text'],
        num_rows: 10
    })
})

## Tokenize Data

In [7]:
model_name = 'HuggingFaceTB/SmolLM-360M'
tokenizer = AutoTokenizer.from_pretrained(model_name)
tokenizer.pad_token = tokenizer.eos_token
print(tokenizer.eos_token)

def preprocess_function(examples):
    #add eos token
    examples["text"] = [text + tokenizer.eos_token for text in examples["text"]]
    ids = tokenizer(examples["text"], padding="max_length", truncation=True, max_length=1024, padding_side="right")
    
    return ids

tokenized_datasets = dataset.map(preprocess_function, batched=True)

tokenized_datasets["train"] = tokenized_datasets["train"].map(lambda x: {"labels": x["input_ids"]}, batched=True)
tokenized_datasets["test"] = tokenized_datasets["test"].map(lambda x: {"labels": x["input_ids"]}, batched=True)

<|endoftext|>


Map: 100%|██████████| 10/10 [00:00<00:00, 293.41 examples/s]


In [8]:
#Save the tokenized dataset
tokenized_datasets.save_to_disk(f'tokenized_v2')

Saving the dataset (1/1 shards): 100%|██████████| 10/10 [00:00<00:00, 761.20 examples/s]


## Distillation Config

In [14]:
# Configuración
teacher_model_name = "HuggingFaceTB/SmolLM-1.7B"  # Modelo teacher grande
batch_size = 4
num_epochs = 1
learning_rate = 5e-5
temperature = 2.0
loss_lambda = 0.7  # Balance entre pérdida de teacher y ground truth
max_length = 512  # Longitud máxima de secuencia
#device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device="cpu"
print(f"Usando dispositivo: {device}")


Usando dispositivo: cpu


In [15]:
# Inicializar modelos
teacher = AutoModelForCausalLM.from_pretrained(teacher_model_name)

Loading checkpoint shards: 100%|██████████| 2/2 [00:01<00:00,  1.71it/s]


In [32]:
for param in teacher.parameters():
    param.requires_grad = False

# loss function for Knowledge Distillation
def kl_divergence_loss(student_logits, teacher_logits, temperature):
    student_probs = torch.nn.functional.log_softmax(student_logits / temperature, dim=-1)
    teacher_probs = torch.nn.functional.softmax(teacher_logits / temperature, dim=-1)
    return torch.nn.functional.kl_div(student_probs, teacher_probs, reduction="batchmean") * (temperature ** 2)

# Function to calculate the total loss.
def compute_loss(student_outputs, teacher_outputs, labels, loss_lambda, temperature):
    # Standard loss (cross-entropy with the labels).
    ce_loss = student_outputs.loss
    # Distillation loss (KL divergence with the teacher).
    kd_loss = kl_divergence_loss(
        student_outputs.logits, 
        teacher_outputs.logits, 
        temperature
    )
    # Total loss
    total_loss = (1 - loss_lambda) * ce_loss + loss_lambda * kd_loss
    return total_loss, ce_loss, kd_loss

In [34]:
def distill_model(global_model,
                  dataloader_train,
                  batch_size,
                 num_epochs,
                 learning_rate,
                 temperature,
                 loss_lambda,
                 max_length,
                 optimizer_kd,
                 scheduler_kd):
    global_model.to(device)
    print("\n\nTraining student with teacher...")
    for epoch in range(num_epochs):
        print(f"KD Epoch  {epoch + 1}/{num_epochs}:")
        global_model.train()
        total_loss = 0
        total_ce_loss = 0
        total_kd_loss = 0
        
        for batch in tqdm(dataloader_train):
            input_ids_list = batch["input_ids"]
            input_ids = torch.stack(input_ids_list, dim=1)  # dim=1 para (seq_len, batch_size)
            input_ids = input_ids.transpose(0, 1)  # Ahora es (batch_size, seq_len)
            attention_mask_list = batch["attention_mask"]
            attention_mask = torch.stack(attention_mask_list, dim=1)  # dim=1 para (seq_len, batch_size)
            attention_mask = attention_mask.transpose(0, 1)  # Ahora es (batch_size, seq_len)
            
            labels_list = batch["labels"]
            labels = torch.stack(labels_list, dim=1)  # dim=1 para (seq_len, batch_size)
            labels = labels.transpose(0, 1)  # Ahora es (batch_size, seq_len)
            # Forward pass del teacher
            with torch.no_grad():
                teacher_outputs = teacher(
                    input_ids=input_ids.to(device),
                    attention_mask=attention_mask.to(device),
                    labels=labels.to(device)
                )
            
            # Forward pass del student
            student_outputs = global_model(
                input_ids=input_ids.to(device),
                attention_mask=attention_mask.to(device),
                labels=labels.to(device)
            )
            # Calculate loss
            loss, ce_loss, kd_loss = compute_loss(
                student_outputs, teacher_outputs, labels, loss_lambda, temperature
            )
            print(loss)
            # Backward pass
            loss.backward()
            torch.nn.utils.clip_grad_norm_(global_model.parameters(), 1.0)
            optimizer_kd.step()
            scheduler_kd.step()
            optimizer_kd.zero_grad()
            
            # Estadísticas
            total_loss += loss.item()
            total_ce_loss += ce_loss.item()
            total_kd_loss += kd_loss.item()
        
        avg_loss = total_loss / len(dataloader_train)
        avg_ce_loss = total_ce_loss / len(dataloader_train)
        avg_kd_loss = total_kd_loss / len(dataloader_train)
        
        print(f"Train Loss: {avg_loss:.4f} (CE: {avg_ce_loss:.4f}, KD: {avg_kd_loss:.4f})")
        return global_model
        ################ End Distill Lora Params of Global Model############

## Train the model

In [35]:
# Initialize variables
SIM_NAME = "Experimento 01"
NUM_ROUNDS = 5
NUM_CLIENTS = 2
CLIENT_FRAC = 1
MODEL_NAME = "HuggingFaceTB/SmolLM-135M"
path = "tokenized_v2"
lora = True
lora_rank = 8
nrows = None
max_steps = 5
batch_size = 1

In [ ]:
### Import global and Student model
global_model, tokenizer = initialize_model(MODEL_NAME, lora_rank=lora_rank, sim_name=SIM_NAME, lora = lora) 
rs = random.SystemRandom()

In [20]:
tokenized_datasets = load_dataset(path, nrows=nrows)

In [21]:
clients_dataset = split_data(tokenized_datasets, NUM_CLIENTS, SIM_NAME)

Saving the dataset (1/1 shards): 100%|██████████| 5/5 [00:00<00:00, 71.68 examples/s]


Saving the dataset (1/1 shards): 100%|██████████| 5/5 [00:00<00:00, 122.91 examples/s]


In [22]:
train_client

<function utils_final.train_client(client, client_dataset, round, sim_name, tokenizer, epochs=1, batch_size=2, max_steps=100, lr=0.002, model_name='HuggingFaceTB/SmolLM-360M', lora=True)>

In [23]:
dataloader_train = DataLoader(tokenized_datasets["train"], batch_size=2, shuffle=True)
dataloader_eval = DataLoader(tokenized_datasets["test"], batch_size=2, shuffle=True)

In [ ]:
### CONFIG FOR TRAIN DISTILL MODEL
optimizer_kd = AdamW(global_model.parameters(), lr=learning_rate)
total_steps_kd = len(tokenized_datasets["train"]) * num_epochs
scheduler_kd = get_linear_schedule_with_warmup(
    optimizer_kd, num_warmup_steps=0, num_training_steps=total_steps_kd
)


In [ ]:
for round in range(1, NUM_ROUNDS+1):

    #Select Clients
    clients = rs.sample(list(range(NUM_CLIENTS)), int(NUM_CLIENTS*CLIENT_FRAC))
    #clients = [0,1]
    
    print(f"Exp: {SIM_NAME} - Round {round}: Clients Selected {clients}")

    # Train clients
    clients_models = []
    for client in clients:
        ## El learning rate va disminuyendo de acuerdo al round en ejecucion, mas en los primero rouds y menos en los siguientes
        new_lr = cosine_learning_rate(current_round = round, total_rounds = NUM_ROUNDS, initial_lr=1e-3, min_lr=1e-5)
        print(f"Round {round}: Training Client {client} with lr {new_lr}")

        client_dataset = Dataset.load_from_disk(f"./fl-results/{SIM_NAME}/round_0/client_{client}")
        client_model = train_client(
            int(client), client_dataset, round, SIM_NAME, tokenizer,
            max_steps=max_steps, lr=new_lr, batch_size=batch_size, model_name=MODEL_NAME,
            lora=lora
        )
        
        clients_models.append(client_model)
        print(f"Round {round}: Client {client} trained")

    # Aggregate model
    aggregated_adapters = aggregate_models(clients_models, lora = lora)
    if lora:
        set_adapters(global_model, aggregated_adapters)
        
        ########## Distilling  global model Here ########
        global_model = distill_model(global_model,
                                     dataloader_train,
                                     batch_size,
                                     num_epochs,
                                     learning_rate,
                                     temperature,
                                     loss_lambda,
                                     max_length,
                                     optimizer_kd,
                                     scheduler_kd)
        ########## Distilling  global model Here ########
        
        save_global_model(global_model, round, SIM_NAME)
    else:
        save_global_model(aggregated_adapters, round, SIM_NAME)

Exp: Experimento 01 - Round 1: Clients Selected [0, 1]
Round 1: Training Client 0 with lr 0.000905463412215599
entro a esta funcon


The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.
`low_cpu_mem_usage` was None, now default to True since model is quantized.
/home/msc2024/ra214616/ra214616_files/gabriel_fl_finetuning/venv/lib/python3.10/site-packages/transformers/training_args.py:1568: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/home/msc2024/ra214616/ra214616_files/gabriel_fl_finetuning/FL-LLM-AD/utils_final.py:159: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `CustomTrainer.__init__`. Use `processing_class` instead.
  super().__init__(**kwargs)
max_steps is given, it will override any value given in num_train_epochs
/home/msc2024/ra214616/ra214616_files/gabriel_fl_finetuning/venv/lib/python3.10/site-packages/bitsandbytes/nn/modules.

OutOfMemoryError: CUDA out of memory. Tried to allocate 960.00 MiB. GPU 0 has a total capacity of 23.67 GiB of which 482.00 MiB is free. Process 427906 has 13.41 GiB memory in use. Process 1372774 has 574.00 MiB memory in use. Process 1431753 has 650.00 MiB memory in use. Process 1448591 has 896.00 MiB memory in use. Including non-PyTorch memory, this process has 7.70 GiB memory in use. Of the allocated memory 7.24 GiB is allocated by PyTorch, and 157.34 MiB is reserved by PyTorch but unallocated. If reserved but unallocated memory is large try setting PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True to avoid fragmentation.  See documentation for Memory Management  (https://pytorch.org/docs/stable/notes/cuda.html#environment-variables)

## Validation Model

In [77]:
import os
import pandas as pd
import torch
from transformers import AutoTokenizer
from peft import PeftModel
import pandas as pd
import numpy as np
from sklearn.metrics import f1_score, precision_score, recall_score
import warnings
from transformers import AutoTokenizer, AutoModelForCausalLM, AutoModelForMaskedLM
import torch
import argparse
from typing import Dict, List
from torch.nn.utils.rnn import pad_sequence
import warnings

In [78]:
# Configuration
SIM_NAME = "Experimento 01"
model_name = "HuggingFaceTB/SmolLM-135M"
dataset_path = "test.csv"
nrows = None
N_ROUNDS = 5
lora = True
RES_NAME = f"{SIM_NAME}_complete"
print(device)

cuda


In [87]:
def is_in_top_k(top_k, target):
    #implement in efficient way
    return target in top_k

In [88]:
def next_token_top_k(data, model, tokenizer,):

    """
    Predict the next token for a given text using a llm model.
    Calculate with the correct token is in the top k predictions.
    """
    accuracies = {'top1':[], 'top3':[], 'top5':[], 'top10':[]}

    model.to(device)
    with torch.no_grad():
        for text in data["text"]:
            
            inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=1024, padding_side="right")
            inputs = {key: inputs[key].to(device) for key in inputs}

            outputs = model(**inputs)
            logits = outputs.logits

            for k in [1, 3, 5, 10]:
                top_k = torch.topk(logits, k, dim=-1).indices
                top_k = top_k.cpu().numpy() 
                
                tokens = inputs['input_ids'][0].cpu().numpy()
                correct = sum(is_in_top_k(top_k[0], token) for token in tokens)

                accuracies[f'top{k}'].append(correct/len(tokens))
        
    return accuracies

In [89]:
data = pd.read_csv(dataset_path, nrows=nrows)
#shuffle data
data = data.sample(frac=1, random_state=0).reset_index(drop=True)


In [90]:
#get 50/50 of each class
data = pd.concat([data[data['Label'] == 1].head(1000), data[data['Label'] == 0].head(1000)])

print(len(data[data['Label'] == 1]), len(data[data['Label'] == 0]))


1000 1000


In [91]:
labels = data["Label"].tolist()
data = data["Content"].tolist()

In [92]:
data = [str(i) for i in data]
dataset_dic = {"text": data}


In [93]:
df_acc = pd.DataFrame()
df_acc.to_csv(f"results_accs_{RES_NAME}.csv", index=False)
df_f1 = pd.DataFrame()
df_f1.to_csv(f"results_f1_{RES_NAME}.csv", index=False)

In [94]:
for round in range(1, N_ROUNDS+1):
    
    if round == 0:
        round = 1

    lora_path = f"fl-results/{SIM_NAME}/round_{round}/global_model"

    model_pretrained = AutoModelForCausalLM.from_pretrained(model_name)
    tokenizer = AutoTokenizer.from_pretrained(model_name)
    tokenizer.pad_token = tokenizer.eos_token

    if lora:
        model_ft = PeftModel.from_pretrained(model_pretrained, lora_path)
        model_ft.to(device)
    else:
        model_ft = AutoModelForCausalLM.from_pretrained(lora_path)

    accuracies = next_token_top_k(dataset_dic, model_ft, tokenizer)
    for k in [1, 3, 5, 10]:

        df_results = pd.DataFrame(accuracies)
        df_results['label'] = labels
        df_results['round'] = round 
        df_results['k'] = k
    
        df_acc = pd.concat([df_acc, df_results])

        df_acc.to_csv(f"results_accs_{RES_NAME}.csv", index=False)

        ths = np.linspace(0, 1, 1000)

        best_f1 = 0
        best_th = 0

        for th in ths:
            df_results['pred'] = df_results[f'top{k}'] < th
            df_results['pred'] = df_results['pred'].astype(int)

            f1 = f1_score(df_results['label'], df_results['pred'])
            precision = precision_score(df_results['label'], df_results['pred'])
            recall = recall_score(df_results['label'], df_results['pred'])

            if f1 > best_f1:
                best_f1 = f1
                best_th = th

        df_results['pred'] = df_results[f'top{k}'] < best_th
        df_results['pred'] = df_results['pred'].astype(int)

        f1 = f1_score(df_results['label'], df_results['pred'])
        precision = precision_score(df_results['label'], df_results['pred'])
        recall = recall_score(df_results['label'], df_results['pred'])

        print(f'Round: {round}')
        print(f'K: {k}')
        print(f'Threshold: {best_th}')
        print(f'F1: {f1}')
        print(f'Precision: {precision}')
        print(f'Recall: {recall}')

        df_f1 = pd.concat([df_f1, pd.DataFrame({"round": [round], "k": [k], "threshold": [best_th], "f1": [f1], "precision": [precision], "recall": [recall]})])
        df_f1.to_csv(f"results_f1_{RES_NAME}.csv", index=False)

/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.p

Round: 1
K: 1
Threshold: 0.985985985985986
F1: 0.8589555880917521
Precision: 0.8388941849380362
Recall: 0.88


/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.p

Round: 1
K: 3
Threshold: 0.993993993993994
F1: 0.9107429182255479
Precision: 0.9781859931113662
Recall: 0.852


/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.p

...

Round: 5
K: 3
Threshold: 0.995995995995996
F1: 0.9383350462487153
Precision: 0.9651162790697675
Recall: 0.913


/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.p

Round: 5
K: 5
Threshold: 0.995995995995996
F1: 0.928234677841802
Precision: 0.9746974697469747
Recall: 0.886


/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/venv/main/lib/python3.10/site-packages/sklearn/metrics/_classification.p

Round: 5
K: 10
Threshold: 1.0
F1: 0.9008145663632008
Precision: 0.8647654093836247
Recall: 0.94


## Plot Graphs

In [95]:
results =  pd.read_csv("results_accs_Experimento 01_complete.csv")
results.head()

top1      top3      top5     top10  label  round  k
0  0.825688  0.917431  0.926606  0.944954      1      1  1
1  0.970361  0.988402  0.988402  0.996134      1      1  1
2  0.986569  0.993895  0.996337  0.998779      1      1  1
3  0.711538  0.788462  0.826923  0.865385      1      1  1
4  0.974026  0.991342  0.991342  0.997114      1      1  1

In [105]:
results.loc[(results["round"]==1) & (results["k"]==5) & (results["label"]==1)]

top1      top3      top5     top10  label  round  k
4000  0.825688  0.917431  0.926606  0.944954      1      1  5
4001  0.970361  0.988402  0.988402  0.996134      1      1  5
4002  0.986569  0.993895  0.996337  0.998779      1      1  5
4003  0.711538  0.788462  0.826923  0.865385      1      1  5
4004  0.974026  0.991342  0.991342  0.997114      1      1  5
...        ...       ...       ...       ...    ...    ... ..
4995  0.977186  0.986692  0.990494  0.994297      1      1  5
4996  0.983246  0.995812  0.996859  0.998953      1      1  5
4997  0.711538  0.788462  0.826923  0.865385      1      1  5
4998  0.978369  0.991681  0.993344  0.995008      1      1  5
4999  0.725490  0.843137  0.882353  0.941176      1      1  5

[1000 rows x 7 columns]

In [97]:
results["round"].unique()

array([1, 2, 3, 4, 5])

In [99]:
results_f1 =  pd.read_csv("results_f1_Experimento 01_complete.csv")
results_f1.head()

round   k  threshold        f1  precision  recall
0      1   1   0.985986  0.858956   0.838894   0.880
1      1   3   0.993994  0.910743   0.978186   0.852
2      1   5   0.996997  0.928535   0.941418   0.916
3      1  10   1.000000  0.898018   0.869036   0.929
4      2   1   0.982983  0.874814   0.865818   0.884

In [103]:
print("precision: ",results_f1["precision"].mean())
print("f1: ",results_f1["f1"].mean())
print("recall: ",results_f1["recall"].mean())

precision:  0.9162027376764783
f1:  0.8996810600408637
recall:  0.8869999999999999
